In [ ]:
# mount drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# update working directory
import sys
sys.path.append('/content/drive/MyDrive/Colab Notebooks/Licenta/SAM-DeepfakeLocalization-local')

In [ ]:
!pip install tensorboardX
!pip install torchmetrics
!{sys.executable} -m pip install 'git+https://github.com/facebookresearch/sam2.git' # colab

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 8.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 961.5/961.5 kB 52.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 123.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 82.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 58.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 43.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 19.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 110.2 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlin

In [ ]:
import os
import time
import torch.multiprocessing
from copy import deepcopy
from tqdm import tqdm
import shutil

from parameters import Parameters
from train.trainer import Trainer
from deepfake_datasets.datasets import get_dataloader
from train.early_stopping import EarlyStopping
from train.validate import validate_detection, validate_fully_supervised_localization
from utils.utils import compute_mean_iou, compute_mean_ap, compute_mean_f1, compute_mean_acc_detection, compute_mean_ap_detection, compute_batch_iou, compute_batch_localization_f1, compute_batch_ap, compute_accuracy_detection, compute_average_precision_detection

In [ ]:
!mkdir -p ../checkpoints/
!wget -P ../checkpoints/ https://dl.fbaipublicfiles.com/segment_anything_2/092824/sam2.1_hiera_small.pt

--2025-05-03 16:14:24--  https://dl.fbaipublicfiles.com/segment_anything_2/092824/sam2.1_hiera_small.pt
Resolving dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)... 13.33.45.114, 13.33.45.45, 13.33.45.5, ...
Connecting to dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)|13.33.45.114|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 184416285 (176M) [application/vnd.snesdev-page-table]
Saving to: ‘../checkpoints/sam2.1_hiera_small.pt’

sam2.1_hiera_small. 100%[===================>] 175.87M   246MB/s    in 0.7s    

2025-05-03 16:14:25 (246 MB/s) - ‘../checkpoints/sam2.1_hiera_small.pt’ saved [184416285/184416285]



In [ ]:
torch.multiprocessing.set_sharing_strategy('file_system')

In [ ]:
new_dataset_name = 'train_lama_ldm_pluralistic_test_repaint-p2-9k'

zip_path = f'/content/drive/MyDrive/Colab Notebooks/Licenta/DeCLIP-main/datasets_zip/combined_training_for_ood/{new_dataset_name}.zip'
new_content_root_path = f'/content/datasets/dolos_data/celebahq/fake/'

os.makedirs(new_content_root_path, exist_ok=True)

# move the dataset from drive to /content (SSD) for better performance in I/O
import zipfile
with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(new_content_root_path)

In [ ]:
# set parameters
params = Parameters()

# set experiment name
params.experiment_name = 'first_try_training_sam_conv4'

params.arch = 'SAM'

# create output dirs
params.create_output_dirs()

new_root_path = '/content/datasets/dolos_data/celebahq/'
# new_root_path = 'D:\\Python\\DeCLIP-main\\datasets\\dolos_data\\celebahq\\'
new_dataset_name = 'train_lama_ldm_pluralistic_test_repaint-p2-9k'

params.update_dolos_data_paths(new_root_path, new_dataset_name)

# fix the backbone - to train only the decoder
params.fix_backbone = True

# set SAM2 checkpoint and config paths
# params.sam_checkpoint_path = '/content/drive/MyDrive/Colab Notebooks/Licenta/SAM-DeepfakeLocalization-local/models/sam_checkpoints/sam2.1_hiera_large.pt'
#params.sam_config_path = '/content/drive/MyDrive/Colab Notebooks/Licenta/SAM-DeepfakeLocalization-local/models/sam_configs/sam2.1_hiera_l.yaml'
params.sam_checkpoint_path = '../checkpoints/sam2.1_hiera_small.pt'
params.sam_config_path = 'configs/sam2.1/sam2.1_hiera_s.yaml'


# set the feature layer and the decoder type
params.feature_layer = 'high_res_feats_1'
params.decoder_type = 'conv-20'

# set the batch size and num threads
params.batch_size = 32 # batch size 64 results in cuda error for some reason
params.num_threads = 4 # batch_size=32 with 8 workers is somehow worse than with 4 workers

# set the number of epochs
params.num_iter = 20

# loss type
params.loss_type = 'bce'

for key, value in params.__dict__.items():
    print(f"{key}: {value}")

experiment_name: first_try_training_sam_conv4
task_type: fully_supervised_localization
data_label: train
arch: CLIP:ViT-L/14
fix_backbone: True
sam_checkpoint_path: ../checkpoints/sam2.1_hiera_small.pt
sam_config_path: configs/sam2.1/sam2.1_hiera_s.yaml
weight_decay: 0.0
batch_size: 32
num_threads: 4
init_type: normal
init_gain: 0.02
train_dataset: train_lama_ldm_pluralistic_test_repaint-p2-9k
decoder_type: conv-20
feature_layer: high_res_feats_1
early_stop_epochs: 5
optim: adam
beta1: 0.9
lr: 0.001
show_loss_freq: 50
num_iter: 20
data_root_path: /content/datasets/dolos_data/celebahq
train_fake_path: /content/datasets/dolos_data/celebahq/fake/train_lama_ldm_pluralistic_test_repaint-p2-9k/images/train
valid_fake_path: /content/datasets/dolos_data/celebahq/fake/train_lama_ldm_pluralistic_test_repaint-p2-9k/images/valid
test_fake_path: /content/datasets/dolos_data/celebahq/fake/train_lama_ldm_pluralistic_test_repaint-p2-9k/images/test
train_masks_ground_truth_path: /content/datasets/dolos

In [ ]:
# get the model, along with its trainer
model_trainer = Trainer(params)

In [ ]:
# get the dataloaders
train_loader = get_dataloader(params)

val_params = deepcopy(params)
val_params.data_label = 'valid'
val_loader = get_dataloader(val_params)

In [ ]:
# start the training loop
model_trainer.model.verbose = False
# model_trainer.compute_pos_weight_per_dataset(train_loader)
early_stopping = EarlyStopping(patience=params.early_stop_epochs, verbose=True, delta=-0.001)
best_metric = 0.0 # iou for localization, ap for detection
print('Length of training set:', len(train_loader.dataset))
print('Length of validation set:', len(val_loader.dataset))
start_time = time.time()
for epoch in tqdm(range(params.num_iter)):
    print('Epoch:', epoch)

    epoch_loss = 0
    for data in train_loader:
        model_trainer.total_steps += 1

        if model_trainer.total_steps % params.show_loss_freq == 0:
            # model_trainer.model.verbose = True
            print('IOUs: ', model_trainer.ious)
        else:
            model_trainer.model.verbose = False

        model_trainer.set_input(data)
        model_trainer.optimize_parameters()

        if model_trainer.total_steps % params.show_loss_freq == 0:
            epoch_loss += model_trainer.loss.item()
            print(f'Train Loss: {model_trainer.loss.item():.4f} at step {model_trainer.total_steps} \t Iter time: {(time.time() - start_time) / model_trainer.total_steps:.2f}')


    epoch_loss /= len(train_loader.dataset)
    print(f'Average Train Loss: {epoch_loss:.4f}')

    # compute training metrics
    if params.task_type == 'fully_supervised_localization':
        compute_mean_iou(model_trainer.ious, verbose=True, extra_text=f'Train epoch {epoch} ')
        model_trainer.ious = []

        compute_mean_f1(model_trainer.f1_best, model_trainer.f1_fixed, verbose=True, extra_text=f'Train epoch {epoch} ')
        model_trainer.f1_best = []
        model_trainer.f1_fixed = []

        compute_mean_ap(model_trainer.ap, verbose=True, extra_text=f'Train epoch {epoch} ')
        model_trainer.ap = []


    # validate the model
    print('Validation:')
    if params.task_type == 'fully_supervised_localization':
        ious, f1_best, f1_fixed, mean_ap, _ = validate_fully_supervised_localization(model_trainer.model, val_loader, params.train_dataset)

        # compute metrics
        mean_iou = compute_mean_iou(ious, verbose=True, extra_text=f'Validation at epoch {epoch} ')

        mean_f1_best, mean_f1_fixed = compute_mean_f1(f1_best, f1_fixed, verbose=True, extra_text=f'Validation at epoch {epoch} ')

        mean_ap = compute_mean_ap(mean_ap, verbose=True, extra_text=f'Validation at epoch {epoch} ')

        # save the model if the mean iou is improved
        if mean_iou > best_metric:
            best_metric = mean_iou
            model_trainer.save_model(f'best_localization_model_iou_{mean_iou:.4f}.pth')
            print(f'Best model saved at epoch {epoch}!')

        # check for early stopping
        early_stopping(mean_iou)

    # check if early stopping is triggered
    if early_stopping.early_stop:
        print("Early stopping triggered")
        continue_training = model_trainer.adjust_learning_rate()
        if continue_training:
            print("Continuing training with a learning rate reduced by a factor of 10")
            early_stopping = EarlyStopping(patience=params.early_stop_epochs, verbose=True, delta=-0.002) # adjust the delta only once, otherwise stop completely
        else:
            print(f"Early stopping training at epoch {epoch}")
            break
    print()

Length of training set: 9000
Length of validation set: 900


  0%|          | 0/20 [00:00<?, ?it/s]

Epoch: 0
IOUs:  [44.20698285102844, 23.717080056667328, 42.640793323516846, 27.962684631347656, 28.417930006980896, 9.561696648597717, 0.713432440534234, 21.771131455898285, 39.05061483383179, 7.679757475852966, 29.55765128135681, 19.666285812854767, 36.85561418533325, 3.722035139799118, 3.7101391702890396, 2.1411122754216194, 48.82860481739044, 40.90973436832428, 1.3849502429366112, 0.6135471165180206, 0.7251369766891003, 40.13393521308899, 7.425485551357269, 1.2647777795791626, 0.48409956507384777, 44.94438171386719, 2.6613688096404076, 54.0601372718811, 20.767101645469666, 18.872183561325073, 34.93435978889465, 4.302503913640976, 17.958569526672363, 19.24804151058197, 8.86671096086502, 13.90298306941986, 11.177773773670197, 6.385908275842667, 19.529007375240326, 4.171847924590111, 13.641908764839172, 19.50785517692566, 1.0185298509895802, 16.452407836914062, 13.453131914138794, 19.43589895963669, 3.6668680608272552, 2.2460464388132095, 2.5873148813843727, 6.519702821969986, 1.945486


100%|██████████| 29/29 [01:20<00:00,  2.78s/it]


Validation at epoch 0 Mean IOU: 42.8
Validation at epoch 0 Mean F1 best: 0.56
Validation at epoch 0 Mean F1 fixed: 0.4755
Validation at epoch 0 Mean AP: 0.556


...

Validation at epoch 17 Mean IOU: 59.66
Validation at epoch 17 Mean F1 best: 0.76
Validation at epoch 17 Mean F1 fixed: 0.6429
Validation at epoch 17 Mean AP: 0.7764
Early Stopping counter: 1 out of 5

Epoch: 18
IOUs:  [94.59747672080994, 95.56708931922913, 96.04886174201965, 9.813542339864867e-10, 88.72671723365784, 17.080460488796234, 84.74043011665344, 0.2475247485563159, 94.16556358337402, 97.31806516647339, 90.48831462860107, 13.514705002307892, 36.79805099964142, 29.95971441268921, 96.77786827087402, 2.3635073932715134e-10, 84.35754179954529, 93.69685649871826, 74.44245219230652, 91.63089394569397, 21.63521945476532, 82.30948448181152, 96.20391130447388, 0.17934002680703998, 73.08598160743713, 76.93912982940674, 95.85664868354797, 68.3059573173523, 8.976660560711114e-10, 53.564369678497314, 84.60019826889038, 80.66037893295288, 97.56477475166321, 97.32748866081238, 3.532998636364937, 5.958981066942215, 0.22519987542182207, 77.61802077293396, 83.46859216690063, 95.49514055252075, 4


 95%|█████████▌| 19/20 [4:44:33<14:57, 897.09s/it]

Validation at epoch 18 Mean IOU: 59.18
Validation at epoch 18 Mean F1 best: 0.7853
Validation at epoch 18 Mean F1 fixed: 0.6783
Validation at epoch 18 Mean AP: 0.7746
Early Stopping counter: 2 out of 5

Epoch: 19
IOUs:  [97.95506000518799, 0.8623922243714333, 67.94453263282776, 24.02622103691101, 54.80167269706726, 97.15776443481445, 94.93594169616699, 5.211574211716652, 80.88803291320801, 8.594369888305664, 95.2934741973877, 90.28883576393127, 67.60274171829224, 69.37217116355896, 92.63388514518738, 73.68708848953247, 97.85414934158325, 95.24325728416443, 8.15545842051506, 40.54684937000275, 16.373521089553833, 86.64615154266357, 95.71780562400818, 97.40678071975708, 94.84249353408813, 24.884793162345886, 31.869369745254517, 95.81292867660522, 65.31751751899719, 68.27920079231262, 7.105942815542221, 85.20368933677673, 93.83957982063293, 93.07498931884766, 16.812609136104584, 91.00998640060425, 84.38055515289307, 30.4904043674469, 2.4390242993831635, 75.45454502105713, 36.8366271257400


100%|██████████| 20/20 [4:59:32<00:00, 898.63s/it]

Validation at epoch 19 Mean IOU: 55.14
Validation at epoch 19 Mean F1 best: 0.7314
Validation at epoch 19 Mean F1 fixed: 0.5666
Validation at epoch 19 Mean AP: 0.7583
Early Stopping counter: 3 out of 5



In [ ]:
from google.colab import files
model_dir = '/content/experiments/first_try_training_sam_conv4/models/'
model_files = sorted(
    [f for f in os.listdir(model_dir) if f.endswith('.pth')]
)

best_model = model_files[-1]
best_model_path = os.path.join(model_dir, best_model)

files.download(best_model_path)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>